<a href="https://colab.research.google.com/github/NickStrauch13/beverage-recommender/blob/tom/beer_ncf.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
! pip install -q kaggle

In [2]:
from google.colab import files

files.upload()
print("files done")

ModuleNotFoundError: No module named 'google.colab'

In [ ]:
! mkdir ~/.kaggle

! cp kaggle.json ~/.kaggle/

In [ ]:
! chmod 600 ~/.kaggle/kaggle.json

In [ ]:
! kaggle datasets list

ref                                                           title                                            size  lastUpdated          downloadCount  voteCount  usabilityRating  
------------------------------------------------------------  ----------------------------------------------  -----  -------------------  -------------  ---------  ---------------  
sudarshan24byte/online-food-dataset                           Online Food Dataset                               3KB  2024-03-02 18:50:30          24897        495  0.9411765        
sukhmandeepsinghbrar/most-subscribed-youtube-channel          Most Subscribed YouTube Channel                   1KB  2024-04-10 20:33:05            792         30  1.0              
sanyamgoyal401/customer-purchases-behaviour-dataset           Customer Purchases Behaviour Dataset              1MB  2024-04-06 18:42:01           1328         34  1.0              
mohdshahnawazaadil/credit-card-dataset                        Credit Card Dataset         

In [ ]:
!kaggle datasets download -d rdoume/beerreviews

 91% 25.0M/27.4M [00:01<00:00, 28.8MB/s]
100% 27.4M/27.4M [00:01<00:00, 21.6MB/s]


In [ ]:
!unzip beerreviews.zip

Archive:  beerreviews.zip
  inflating: beer_reviews.csv        


In [42]:
import pandas as pd
df = pd.read_csv('../../data/beer_reviews.csv')

In [43]:
df.describe()

brewery_id   review_time  review_overall  review_aroma  \
count  1.586614e+06  1.586614e+06    1.586614e+06  1.586614e+06   
mean   3.130099e+03  1.224089e+09    3.815581e+00  3.735636e+00   
std    5.578104e+03  7.654427e+07    7.206219e-01  6.976167e-01   
min    1.000000e+00  8.406720e+08    0.000000e+00  1.000000e+00   
25%    1.430000e+02  1.173224e+09    3.500000e+00  3.500000e+00   
50%    4.290000e+02  1.239203e+09    4.000000e+00  4.000000e+00   
75%    2.372000e+03  1.288568e+09    4.500000e+00  4.000000e+00   
max    2.800300e+04  1.326285e+09    5.000000e+00  5.000000e+00   

       review_appearance  review_palate  review_taste      beer_abv  \
count       1.586614e+06   1.586614e+06  1.586614e+06  1.518829e+06   
mean        3.841642e+00   3.743701e+00  3.792860e+00  7.042387e+00   
std         6.160928e-01   6.822184e-01  7.319696e-01  2.322526e+00   
min         0.000000e+00   1.000000e+00  1.000000e+00  1.000000e-02   
25%         3.500000e+00   3.500000e+00  3.500000e+00  5.200000e+00   
50%         4.000000e+00   4.000000e+00  4.000000e+00  6.500000e+00   
75%         4.000000e+00   4.000000e+00  4.500000e+00  8.500000e+00   
max         5.000000e+00   5.000000e+00  5.000000e+00  5.770000e+01   

        beer_beerid  
count  1.586614e+06  
mean   2.171279e+04  
std    2.181834e+04  
min    3.000000e+00  
25%    1.717000e+03  
50%    1.390600e+04  
75%    3.944100e+04  
max    7.731700e+04

In [ ]:
!pip install tensorflow pandas numpy scikit-learn

In [44]:
ndf = df[['review_profilename', 'beer_beerid', 'review_overall']]

In [45]:
print("Missing values before handling:")
print(ndf.isnull().sum())

ndf = ndf.dropna()
print("Missing values after handling:")
print(ndf.isnull().sum())

print(ndf.head())

Missing values before handling:
review_profilename    348
beer_beerid             0
review_overall          0
dtype: int64
Missing values after handling:
review_profilename    0
beer_beerid           0
review_overall        0
dtype: int64
  review_profilename  beer_beerid  review_overall
0            stcules        47986             1.5
1            stcules        48213             3.0
2            stcules        48215             3.0
3            stcules        47969             3.0
4     johnmichaelsen        64883             4.0


In [53]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder
import tensorflow as tf
from keras import layers, Model
from keras.optimizers import Adam

In [54]:
# Create a dictionary mapping beer IDs to names
beer_id_to_name = pd.Series(df.beer_name.values, index=df.beer_beerid).to_dict()

# Encode 'review_profilename' and 'beer_beerid'
user_encoder = LabelEncoder()
item_encoder = LabelEncoder()

ndf['user_encoded'] = user_encoder.fit_transform(ndf['review_profilename'])
ndf['item_encoded'] = item_encoder.fit_transform(ndf['beer_beerid'])

# Split the dataset
train, test = train_test_split(ndf, test_size=0.2, random_state=42)

In [55]:
from keras import layers, Model
from keras.optimizers import Adam

def create_ncf(num_users, num_items, embedding_size, layer_sizes=[64, 32, 16, 8]):
    # Input layers
    user_input = layers.Input(shape=(1,))
    item_input = layers.Input(shape=(1,))

    # Embeddings layers
    user_embedding_gmf = layers.Embedding(num_users, embedding_size, embeddings_initializer='he_normal',
                                          embeddings_regularizer=tf.keras.regularizers.l2(1e-6))(user_input)
    user_embedding_gmf = layers.Flatten()(user_embedding_gmf)

    item_embedding_gmf = layers.Embedding(num_items, embedding_size, embeddings_initializer='he_normal',
                                          embeddings_regularizer=tf.keras.regularizers.l2(1e-6))(item_input)
    item_embedding_gmf = layers.Flatten()(item_embedding_gmf)

    user_embedding_mlp = layers.Embedding(num_users, embedding_size, embeddings_initializer='he_normal',
                                          embeddings_regularizer=tf.keras.regularizers.l2(1e-6))(user_input)
    user_embedding_mlp = layers.Flatten()(user_embedding_mlp)

    item_embedding_mlp = layers.Embedding(num_items, embedding_size, embeddings_initializer='he_normal',
                                          embeddings_regularizer=tf.keras.regularizers.l2(1e-6))(item_input)
    item_embedding_mlp = layers.Flatten()(item_embedding_mlp)

    # GMF part
    gmf_mul = layers.Multiply()([user_embedding_gmf, item_embedding_gmf])

    # MLP part
    mlp_concat = layers.Concatenate()([user_embedding_mlp, item_embedding_mlp])
    mlp = mlp_concat
    for layer_size in layer_sizes:
        mlp = layers.Dense(layer_size, activation='relu')(mlp)

    # Concatenate GMF and MLP parts
    concat = layers.Concatenate()([gmf_mul, mlp])

    # Final prediction layer scaled to 0-5 range
    output = layers.Dense(1, activation='linear')(concat)
    output = layers.Lambda(lambda x: x * 5)(output)

    model = Model(inputs=[user_input, item_input], outputs=output)
    model.compile(optimizer=Adam(learning_rate=0.00005), loss='mse', metrics=['mae'])

    return model


In [56]:
# Instantiate and train the model
num_users = ndf['user_encoded'].nunique()
num_items = ndf['item_encoded'].nunique()
embedding_size = 256
model = create_ncf(num_users, num_items, embedding_size)
model.summary()

# Preparing the data
x_train = [train['user_encoded'].values, train['item_encoded'].values]
y_train = train['review_overall'].values

# Training the model
history = model.fit(x_train, y_train, batch_size=128, epochs=1, validation_split=0.2)

Model: "model_6"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_13 (InputLayer)       [(None, 1)]                  0         []                            
                                                                                                  
 input_14 (InputLayer)       [(None, 1)]                  0         []                            
                                                                                                  
 embedding_26 (Embedding)    (None, 1, 256)               8547072   ['input_13[0][0]']            
                                                                                                  
 embedding_27 (Embedding)    (None, 1, 256)               1690905   ['input_14[0][0]']            
                                                          6                                 

2024-04-15 19:09:59.309507: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:961] model_pruner failed: INVALID_ARGUMENT: Graph does not contain terminal node Adam/AssignAddVariableOp.


7932/7932 [==============================] - 324s 41ms/step - loss: 0.9841 - mae: 0.6464 - val_loss: 0.3905 - val_mae: 0.4682


In [57]:
# Preparing the data
x_test = [test['user_encoded'].values, test['item_encoded'].values]
y_test = test['review_overall'].values  # Use actual ratings

# Evaluate the model using regression metrics
test_loss, test_mae = model.evaluate(x_test, y_test)
print(f'Test MSE: {test_loss}, Test MAE: {test_mae}')

# save model
model.save('../../models/ncf_model2.h5')

9915/9915 [==============================] - 121s 12ms/step - loss: 0.3866 - mae: 0.4668
Test MSE: 0.386563241481781, Test MAE: 0.466751366853714


/Users/nicholasconterno/Library/Python/3.9/lib/python/site-packages/keras/src/engine/training.py:3079: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


In [34]:
import numpy as np
import pandas as pd

# Example setup
user_to_predict = 'stcules'
beers_to_predict = [47986, 64883,232]

# Ensure that user_encoder and item_encoder are already defined and fitted
# Transform the user string to index using LabelEncoder
user_index = user_encoder.transform([user_to_predict])[0]

# Iterate over the list of beer IDs to predict
for beer_id in beers_to_predict:
    # Transform the beer ID to index
    try:
        item_index = item_encoder.transform([beer_id])[0]
        # Make the prediction using the transformed indices
        prediction = model.predict([np.array([user_index]), np.array([item_index])])

        # Fetch the beer name using the ID, default to 'Unknown Beer' if ID is not found
        beer_name = beer_id_to_name.get(beer_id, 'Unknown Beer')

        # Print the prediction
        print(f"Predicted rating for {beer_name} (ID: {beer_id}): {prediction[0][0]:.2f}")
    except ValueError:
        print(f"Beer ID {beer_id} not found in the training data.")


1/1 [==============================] - 0s 99ms/step
Predicted rating for Sausa Weizen (ID: 47986): 2.76
1/1 [==============================] - 0s 16ms/step
Predicted rating for Cauldron DIPA (ID: 64883): 3.11
1/1 [==============================] - 0s 16ms/step
Predicted rating for Corona Extra (ID: 232): 2.27


In [35]:
# function to get the top N recommendations for a user
def get_top_n_recommendations(user_index, n=10):
    # Create a list of all beer indices
    all_beer_indices = np.arange(num_items)

    # Remove the beers that the user has already rated
    beers_rated = ndf[ndf['user_encoded'] == user_index]['item_encoded'].values
    beers_unrated = np.setdiff1d(all_beer_indices, beers_rated)

    # Make a prediction for the user on all unrated beers
    user_indices = np.array([user_index] * len(beers_unrated))
    predictions = model.predict([user_indices, beers_unrated])

    # Get the indices that would sort the predictions array
    sorted_indices = np.argsort(predictions, axis=0)[::-1].flatten()

    # Get the top N recommendations
    top_n_indices = beers_unrated[sorted_indices][:n]

    # Convert the beer indices back to beer IDs
    top_n_beer_ids = item_encoder.inverse_transform(top_n_indices)

    # Get the beer names using the IDs
    top_n_beer_names = [beer_id_to_name[beer_id] for beer_id in top_n_beer_ids]
    
    # return the top n predictions

    top_n_predictions = [predictions[i] for i in sorted_indices[:n]]

    return top_n_beer_names, top_n_predictions


# Get the top 10 recommendations for the user 'stcules'
user_index = user_encoder.transform(['brentk56'])[0]
top_n_recommendations, top_n_preds = get_top_n_recommendations(user_index, n=10)

# Print the top 10 recommendations with their predicted ratings
for beer_name, prediction in zip(top_n_recommendations, top_n_preds):
    print(f"{beer_name}: {prediction[0]:.2f}")


1962/1962 [==============================] - 6s 3ms/step
Armand'4 Oude Geuze Lente (Spring): 4.70
Dirty Horse: 4.68
Citra DIPA: 4.62
Geuze Cuvée J&J (Joost En Jessie) Blauw (Blue): 4.62
Heady Topper: 4.59
Oude Lambiek De Cam: 4.58
Drie Fonteinen Oude Geuze Vintage: 4.58
Cantillon Blåbær Lambik: 4.58
Southampton Berliner Weisse: 4.58
Deviation - Bottleworks 9th Anniversary: 4.57


In [ ]:

# print out top 10 users with the most reviews
top_users = ndf['review_profilename'].value_counts().head(10)
print(top_users)



Beer ID: 47986, Beer Name: Sausa Weizen
Beer ID: 48213, Beer Name: Red Moon
Beer ID: 48215, Beer Name: Black Horse Black Beer
Beer ID: 47969, Beer Name: Sausa Pils
Beer ID: 64883, Beer Name: Cauldron DIPA
Beer ID: 52159, Beer Name: Caldera Ginger Beer
Beer ID: 436, Beer Name: Amstel Light
Beer ID: 10789, Beer Name: Caldera Oatmeal Stout
Beer ID: 12386, Beer Name: Caldera OBF 15
Beer ID: 58046, Beer Name: Rauch Ür Bock
Beer ID: 25414, Beer Name: Caldera Pale Ale
Beer ID: 10788, Beer Name: Pilot Rock Porter
Beer ID: 58920, Beer Name: Vas Deferens Ale
Beer ID: 10784, Beer Name: Caldera IPA
Beer ID: 21241, Beer Name: Cauldron Espresso Stout
Beer ID: 20818, Beer Name: Old Growth Imperial Stout
Beer ID: 10786, Beer Name: Dry Hop Red
Beer ID: 10794, Beer Name: Southside Strong
Beer ID: 54330, Beer Name: Caldera Märzen
Beer ID: 20817, Beer Name: Lawnmower Lager
Beer ID: 61427, Beer Name: Caldera Rose Petal (Kettle Series)
Beer ID: 3386, Beer Name: Amstel Bright
Beer ID: 55097, Beer Name: Nut B

In [36]:
# make a prediction for a new user based on their reviews
new_user = 'new_user'
new_reviews = {
    'review_profilename': [new_user] * 5,
    'beer_beerid': [47986, 64883, 232, 412, 100],
    'review_overall': [5, 4, 3, 2, 1]
}

new_df = pd.DataFrame(new_reviews)
#create a new user index by picking the highest index and adding 1
new_user_index = ndf['user_encoded'].max() + 1

# Encode the new user's reviews
new_df['user_encoded'] = new_user_index
new_df['item_encoded'] = item_encoder.transform(new_df['beer_beerid'])

# Make predictions for the new user using get_top_n_recommendations
top_n_recommendations, top_n_preds = get_top_n_recommendations(new_user_index, n=10)

# Print the top 10 recommendations with their predicted ratings
for beer_name, prediction in zip(top_n_recommendations, top_n_preds):
    print(f"{beer_name}: {prediction[0]:.2f}")



2065/2065 [==============================] - 6s 3ms/step
Armand'4 Oude Geuze Lente (Spring): 4.49
Dirty Horse: 4.48
King Henry: 4.45
Trappist Westvleteren 12: 4.42
Citra DIPA: 4.41
Geuze Cuvée J&J (Joost En Jessie) Blauw (Blue): 4.41
Heady Topper: 4.38
Oude Lambiek De Cam: 4.38
Drie Fonteinen Oude Geuze Vintage: 4.38
Cantillon Blåbær Lambik: 4.37


In [37]:
# save the model
model.save('../../models/ncf_model.h5')



/Users/nicholasconterno/Library/Python/3.9/lib/python/site-packages/keras/src/engine/training.py:3079: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


In [39]:
# new function that returns the top n recommendations for a user but only for beers that have not been rated by the user and have at least a certain number of reviews

def get_top_n_recommendations(user_index, n=10, min_reviews=10):
    # Create a list of all beer indices
    all_beer_indices = np.arange(num_items)

    # Remove the beers that the user has already rated
    beers_rated = ndf[ndf['user_encoded'] == user_index]['item_encoded'].values
    beers_unrated = np.setdiff1d(all_beer_indices, beers_rated)

    # Filter out beers with less than min_reviews reviews
    beer_review_counts = ndf['item_encoded'].value_counts()
    beers_unrated = np.array([beer_id for beer_id in beers_unrated if beer_review_counts[beer_id] >= min_reviews])

    # Make a prediction for the user on all unrated beers
    user_indices = np.array([user_index] * len(beers_unrated))
    predictions = model.predict([user_indices, beers_unrated])

    # Get the indices that would sort the predictions array
    sorted_indices = np.argsort(predictions, axis=0)[::-1].flatten()

    # Get the top N recommendations
    top_n_indices = beers_unrated[sorted_indices][:n]

    # Convert the beer indices back to beer IDs
    top_n_beer_ids = item_encoder.inverse_transform(top_n_indices)

    # Get the beer names using the IDs
    top_n_beer_names = [beer_id_to_name[beer_id] for beer_id in top_n_beer_ids]
    
    # return the top n predictions

    top_n_predictions = [predictions[i] for i in sorted_indices[:n]]

    return top_n_beer_names, top_n_predictions


# Get the top 10 recommendations for the user 'stcules' with a minimum of 100 reviews
user_index = user_encoder.transform(['brentk56'])[0]
top_n_recommendations, top_n_preds = get_top_n_recommendations(user_index, n=10, min_reviews=10)

# Print the top 10 recommendations with their predicted ratings
for beer_name, prediction in zip(top_n_recommendations, top_n_preds):
    print(f"{beer_name}: {prediction[0]:.2f}")

349/349 [==============================] - 1s 3ms/step
Armand'4 Oude Geuze Lente (Spring): 4.70
Dirty Horse: 4.68
Citra DIPA: 4.62
Geuze Cuvée J&J (Joost En Jessie) Blauw (Blue): 4.62
Heady Topper: 4.59
Oude Lambiek De Cam: 4.58
Drie Fonteinen Oude Geuze Vintage: 4.58
Cantillon Blåbær Lambik: 4.58
Southampton Berliner Weisse: 4.58
Deviation - Bottleworks 9th Anniversary: 4.57


In [40]:
# save user_encoder and item_encoder
import joblib

joblib.dump(user_encoder, '../../models/user_encoder.pkl')
joblib.dump(item_encoder, '../../models/item_encoder.pkl')


['../../models/item_encoder.pkl']